# コードを使用したテンプレートからホストされたカスタム指標の作成

ホストされたカスタム指標は、DataRobotインフラストラクチャでユーザー指定のコードを実行して、組織のカスタマイズされた指標を計算します。DataRobotは、一般的な指標用にさまざまなテンプレートを提供します。これらの指標は、そのまま、またはユーザー指定の指標の開始点として使用できます。このチュートリアルでは、Python SDKを使用してホストされたカスタム指標を作成します。


## 前提条件
開始する前に、このチュートリアルで使用するすべてのオブジェクトをインポートして、DataRobotクライアントを初期化します。


In [ ]:
import datarobot as dr
from datarobot.enums import HostedCustomMetricsTemplateMetricTypeQueryParams
from datarobot.models.deployment.custom_metrics import HostedCustomMetricTemplate, HostedCustomMetric, \
    HostedCustomMetricBlueprint, CustomMetric, MetricTimestampSpoofing, ValueField, SampleCountField, BatchField
from datarobot.models.registry import JobRun
from datarobot.models.registry.job import Job
from datarobot import Deployment
from datarobot.models.runtime_parameters import RuntimeParameterValue
from datarobot.models.types import Schedule

DataRobotClient(token="<DataRobot API Token>", endpoint="<DataRobot URL>")
gen_ai_deployment_1 = Deployment.get('<Deployment Id>')

## ホストされたカスタム指標テンプレートの一覧表示
ホストされたカスタム指標をテンプレートから作成する前に、新しい指標の基礎として使用するLLM指標テンプレートを取得します。そのために、`metric_type`を指定します。また、デプロイは日本語のテキストを処理するLLMモデルであるため、名前で特定の指標を検索して、検索を`1`の結果に制限します。次のステップ用のテンプレートに結果を保存します。


In [ ]:
templates = HostedCustomMetricTemplate.list(
    search="[JP] Character Count",
    metric_type=HostedCustomMetricsTemplateMetricTypeQueryParams.LLM,
    limit=1,
    offset=0,
)

## 1ステップでホストされたカスタム指標の作成
Locate the custom metric template to create a hosted custom metric. This method is a shortcut, combining two steps to create a new custom metric from the retrieved template: 


1. （`templates`に保存されている）前のステップで取得したテンプレートから、ホストされたカスタム指標用のカスタムジョブを作成します。

2. ホストされたカスタム指標ジョブを、（`gen_ai_deployment_1`に保存されている）前提条件ステップ中に定義したデプロイに接続します。


2つのオブジェクトを作成しているため、テンプレートとデプロイIDに加えて、ジョブ名とカスタム指標名の両方を指定します。さらに、デプロイのジョブスケジュールとランタイムパラメーターのオーバーライドを定義します。


In [ ]:
hosted_custom_metric = HostedCustomMetric.create_from_template(
    template_id=templates[0].id,
    deployment_id=gen_ai_deployment_1.id,
    job_name="Hosted Custom Metric Character Count",
    custom_metric_name="Character Count",
    job_description="Hosted Custom Metric",
    custom_metric_description="LLM Character Count",
    baseline_value=10,
    timestamp=MetricTimestampSpoofing(
        column_name="timestamp",
        time_format="%Y-%m-%d %H:%M:%S",
    ),
    value = ValueField(column_name="value"),
    sample_count=SampleCountField(column_name='Sample Count'),
    batch=BatchField(column_name='Batch'),
    schedule=Schedule(
        day_of_week=[0],
        hour=['*'],
        minute=['*'],
        day_of_month=[12],
        month=[1],
    ),
    parameter_overrides=[RuntimeParameterValue(field_name='DRY_RUN', value="0", type="string")]
)

ホストされたカスタム指標を作成したら、手動実行を開始します。



In [ ]:
job_run = JobRun.create(
        job_id=hosted_custom_metric.custom_job_id
        runtime_parameter_values=[
            RuntimeParameterValue(field_name='DRY_RUN', value="1", type="string"),
            RuntimeParameterValue(field_name='DEPLOYMENT_ID', value=gen_ai_deployment_1.id, type="deployment"),
            RuntimeParameterValue(field_name='CUSTOM_METRIC_ID', value=hosted_custom_metric.id, type="customMetric"),
        ]
    )
    print(job_run.status)

## 2ステップでホストされたカスタム指標の作成
これらのステップは、順番に手動で実行することもできます。これは、カスタムジョブをデプロイに添付する前にカスタム指標のブループリントを編集する場合に役立ちます。ジョブをデプロイに添付すると、ほとんどの設定がブループリントからコピーされます（オーバーライドが指定されていない場合）。ホストされたカスタム指標を手動で作成するには、最初に、（`templates`に保存されている）以前に取得したテンプレートからカスタムジョブを作成します。


In [ ]:
job = Job.create_from_custom_metric_gallery_template(
    template_id=templates[0].id,
    name="Job created from template",
    description="Job created from template"
)

次に、テンプレートによって提供されるデフォルトのブループリントを取得し、編集します。


In [ ]:
blueprint = HostedCustomMetricBlueprint.get(job.id)
print(f"Original directionality: {blueprint.directionality}")

次に、ブループリントのカスタム指標のパラメーターを更新します。


In [ ]:
updated_blueprint = blueprint.update(
    directionality='lowerIsBetter',
    units='characters',
    type='gauge',
    time_step='hour',
    is_model_specific=False
)
print(f"Updated directionality: {updated_blueprint.directionality}")

これで、ホストされたカスタム指標ジョブが作成されます。ショートカットの方法と同様に、ジョブスケジュール、ランタイムパラメーターのオーバーライド、およびこのデプロイに固有のカスタム指標パラメーターを指定できます。


In [ ]:
another_hosted_custom_metric = HostedCustomMetric.create_from_custom_job(
    custom_job_id=job.id,
    deployment_id=gen_ai_deployment_1.id,
    name="Custom metric created in 2 steps",
)

指標を作成して設定した後、ブループリントへの変更がカスタム指標に反映されていることを確認します。




In [ ]:
another_custom_metric = CustomMetric.get(custom_metric_id=another_hosted_custom_metric.id, deployment_id=gen_ai_deployment_1.id)
print(f"Directionality of another custom metric: {another_custom_metric.directionality}")

最後に、カスタム指標ジョブ用の手動ジョブ実行を作成します。


In [ ]:
job_run = JobRun.create(
    job_id=job.id,
    runtime_parameter_values=[
        RuntimeParameterValue(field_name='DRY_RUN', value="1", type="string"),
        RuntimeParameterValue(field_name='DEPLOYMENT_ID', value=gen_ai_deployment_1.id, type="deployment"),
        RuntimeParameterValue(field_name='CUSTOM_METRIC_ID', value=another_hosted_custom_metric.id, type="customMetric"),
    ]
)
print(job_run.status)

## ジョブに関連付けられているホストされたカスタム指標の一覧表示
カスタムジョブに関連付けられているホストされたカスタム指標をすべて一覧表示するには、次のコードを使用します。


In [1]:
hosted_custom_metrics = HostedCustomMetric.list(deployment_id=hosted_custom_metric.custom_job_id)
for metric in hosted_custom_metrics:
    print(metric.name)

## ホストされたカスタム指標の削除
ホストされたカスタム指標を削除し、デプロイからカスタム指標を削除してジョブを保持することで、別のデプロイの指標を作成できます。



In [ ]:
hosted_custom_metric.delete()
another_hosted_custom_metric.delete()

必要に応じて、カスタムジョブ全体を削除できます。そのジョブに関連付けられているカスタム指標がある場合、その指標も削除されます。


In [ ]:
job.delete()